In [21]:
import utils
from skrub import TableReport
from pathlib import Path
import pandas as pd

In [8]:
X, y = utils.get_train_data()

In [46]:
X_transformed = utils._merge_external_data(X)

In [47]:
TableReport(X_transformed)

Processing column  44 / 44


<TableReport: use .open() to display>

In [48]:
pipeline = utils._get_estimator()

In [49]:
pipeline.fit(X,y)

Pipeline(steps=[('function_transformers',
                 Pipeline(steps=[('external_data',
                                  FunctionTransformer(func=<function _merge_external_data at 0x1261d2980>)),
                                 ('date_features',
                                  FunctionTransformer(func=<function _process_datetime_features at 0x1261d0540>))])),
                ('column_transformers',
                 ColumnTransformer(transformers=[('date',
                                                  OneHotEncoder(handle_unknown='ignore'),
                                                  ['year', 'month', 'weekday',
                                                   'day', 'hour', 'is_weekend',
                                                   'is_school_holiday',
                                                   'is_public_holiday']),
                                                 ('cat',
                                                  OneHotEncoder(handle_unknown='ignore'),
                                                  ['counter_name',
                                                   'site_name'])])),
                ('model', Ridge())])

In [50]:
accuracy = pipeline.score(X, y)
print(f"Accuracy: {accuracy}")

Accuracy: 0.6788628248082138


In [51]:
test_data = pd.read_parquet(Path("data") / "final_test.parquet")

In [52]:
test_data_transformed = utils._merge_external_data(test_data)
# test_data_transformed = test_data_transformed.drop(columns=["counter_name", "counter_technical_id", "coordinates", "Past Weather Code 2", "Station Level Pressure (hPa)", "Layer 1 Cloud Base Height (m)"])

In [53]:
TableReport(test_data_transformed)

Processing column  46 / 46


<TableReport: use .open() to display>

In [54]:
y_pred = pipeline.predict(test_data_transformed)

In [55]:
y_pred

array([1.31786448, 1.08782121, 2.07078261, ..., 2.50453058, 2.25974901,
       2.50117526])

In [56]:
df_submition = pd.DataFrame(y_pred, columns=["log_bike_count"])
df_submition.index.name = "Id"

In [57]:
df_submition

log_bike_count
Id                   
0            1.317864
1            1.087821
2            2.070783
3            1.275396
4            1.772787
...               ...
51435        2.575390
51436        2.897080
51437        2.504531
51438        2.259749
51439        2.501175

[51440 rows x 1 columns]

In [58]:
# df_submition.to_csv("/Users/gregzguegue/Downloads/test_pipeline.csv", index=True)